In [14]:
import pandas as pd

In [24]:
df = pd.read_csv('binding_moad/every.csv',header=None,skiprows=2)
df = df.rename(columns={2:'pdb',3: 'ligand_name', 4: 'ligand_valid', 5: 'affinity_quantity',
                        7: 'affinity_val', 8: 'affinity_unit', 9:'smiles'})
#df = df[df['ligand_valid']!='invalid'].copy()

In [25]:
df['is_sep'] = df[1] == 'Family. Representative Entry is '

In [26]:
df['cum_sum'] = df['is_sep'].cumsum()

In [27]:
quantities = ['ki','kd','ka','k1/2','kb']

In [28]:
from pint import UnitRegistry
ureg = UnitRegistry()

def to_uM(affinity_unit):
    try:
        val = ureg(str(affinity_unit[0])+str(affinity_unit[1]))
        return val.m_as(ureg.uM)
    except Exception:
        pass
    
    try:
        val = ureg(str(affinity_unit[0])+str(affinity_unit[1]))
        return 1/val.m_as(1/ureg.uM)
    except Exception:
        pass

In [29]:
groupby = df.groupby('cum_sum')

In [30]:
def group(df):
    pdb = df[df['is_sep']]['pdb'].values
    if len(pdb) > 0:
        pdb = pdb[0]
        df['pdb_ref'] = pdb
    return df[df['ligand_valid']=='valid']
df_expand = groupby.apply(group).reset_index(drop=True)

In [31]:
len(df_expand)

88806

In [34]:
df_expand['affinity_uM'] = df_expand[['affinity_val','affinity_unit']].apply(to_uM,axis=1)

In [35]:
df_filter = df_expand[df_expand['affinity_quantity'].str.lower().isin(quantities)]

In [38]:
len(df_expand)

88806

In [37]:
len(df_filter)

17724

In [47]:
df_complex = pd.read_parquet('data/moad_complex.parquet')
df_complex['name'] = df_complex['name'].str.upper()

In [48]:
df_all = df_filter.merge(df_complex,left_on='pdb_ref',right_on='name')

In [49]:
df_all = df_all[~df_all['affinity_val'].isnull()]

In [50]:
df_all

0    1  pdb  ligand_name ligand_valid affinity_quantity  6  \
0      NaN  NaN  NaN    2PA:C:613        valid                Ki  =   
1      NaN  NaN  NaN    HAE:C:800        valid                Ki  =   
2      NaN  NaN  NaN    ADN:A:901        valid                Kd  =   
3      NaN  NaN  NaN    ADN:B:902        valid                Kd  =   
4      NaN  NaN  NaN    ADN:C:903        valid                Kd  =   
...    ...  ...  ...          ...          ...               ... ..   
17682  NaN  NaN  NaN  MAN NAG:G:1        valid                Ka  =   
17683  NaN  NaN  NaN  MAN NAG:F:1        valid                Ka  =   
17684  NaN  NaN  NaN  NGA NAG:F:1        valid                Ka  =   
17685  NaN  NaN  NaN  NGA NAG:E:1        valid                Ka  =   
17686  NaN  NaN  NaN  NGA NAG:H:1        valid                Ka  =   

       affinity_val affinity_unit  \
0              0.62            nM   
1              2.60            uM   
2             15.00            uM   
3             15.00            uM   
4             15.00            uM   
...             ...           ...   
17682       7860.00          M^-1   
17683       7860.00          M^-1   
17684       5910.00          M^-1   
17685       5910.00          M^-1   
17686       5910.00          M^-1   

                                                  smiles  10  is_sep  cum_sum  \
0                                             NP(=O)(N)O NaN   False        1   
1                                               CC(=O)NO NaN   False        1   
2      c1nc(c2c(n1)n(cn2)[C@H]3[C@@H]([C@@H]([C@H](O3... NaN   False        5   
3      c1nc(c2c(n1)n(cn2)[C@H]3[C@@H]([C@@H]([C@H](O3... NaN   False        5   
4      c1nc(c2c(n1)n(cn2)[C@H]3[C@@H]([C@@H]([C@H](O3... NaN   False        5   
...                                                  ...  ..     ...      ...   
17682                                                NaN NaN   False    10499   
17683                                                NaN NaN   False    10499   
17684                                                NaN NaN   False    10499   
17685                                                NaN NaN   False    10499   
17686                                                NaN NaN   False    10499   

      pdb_ref  affinity_uM  name  \
0        6H8J     0.000620  6H8J   
1        6H8J     2.600000  6H8J   
2        2GL0    15.000000  2GL0   
3        2GL0    15.000000  2GL0   
4        2GL0    15.000000  2GL0   
...       ...          ...   ...   
17682    2WDB   127.226463  2WDB   
17683    2WDB   127.226463  2WDB   
17684    2WDB   169.204738  2WDB   
17685    2WDB   169.204738  2WDB   
17686    2WDB   169.204738  2WDB   

                                                     seq  
0      NYIVPGEYRVAEGEIEINAGREKTTIRVSNTGDRPIQVGSHIHFVE...  
1      NYIVPGEYRVAEGEIEINAGREKTTIRVSNTGDRPIQVGSHIHFVE...  
2      MTDMSIKFELIDVPIPQGTNVIIGQAHFIKTVEDLYEALVTSVPGV...  
3      MTDMSIKFELIDVPIPQGTNVIIGQAHFIKTVEDLYEALVTSVPGV...  
4      MTDMSIKFELIDVPIPQGTNVIIGQAHFIKTVEDLYEALVTSVPGV...  
...                                                  ...  
17682  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
17683  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
17684  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
17685  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  
17686  MGSSHHHHHHSSGLVPRGSHMASNPSLIRSESWQVYEGNEANLLDG...  

[17687 rows x 17 columns]

In [51]:
df_all[['pdb','ligand_name','smiles','name','affinity_uM','seq']].to_parquet('data/moad.parquet')